In [2]:
import requests
from bs4 import BeautifulSoup
import string
from datetime import datetime
import pandas as pd
import json

In [177]:
pd.set_option('display.max_rows', None)

In [3]:
# Woman's page
woman = "https://knowtheorigin.com/collections/women"

In [5]:
products_woman = pd.read_csv('kto.csv')

In [11]:
products_woman = products_woman.drop(['item-vendor'],axis=1)

In [12]:
products_woman

display_name  \
0                      Topanga Recycled PET Bra Plum   
1              Flora Organic Cotton Check Dress Navy   
2        Modelo 89' Recycled Vegan Trainer Off White   
3    Modelo 89' Recycled Vegan Trainer Beige & White   
4              Handy 100% Recycled PET Backpack Rust   
..                                               ...   
711                                        Perry Top   
712                                 Flor Striped Top   
713   Organic Cotton Oversized Sweatshirt Light Grey   
714                          Eva Cork Sling Bag Navy   
715                  Kata Organic Cotton Dress Black   

                                           product_url  \
0    https://knowtheorigin.com/products/copy-of-top...   
1    https://knowtheorigin.com/products/flora-check...   
2    https://knowtheorigin.com/products/copy-of-mod...   
3    https://knowtheorigin.com/products/modelo-89-r...   
4    https://knowtheorigin.com/products/handy-100-r...   
..                                                 ...   
711       https://knowtheorigin.com/products/perry-top   
712  https://knowtheorigin.com/products/flor-stripe...   
713  https://knowtheorigin.com/products/cotton-flee...   
714  https://knowtheorigin.com/products/eva-cork-sl...   
715    https://knowtheorigin.com/products/black-kata-1   

                                      image_color_link          price  
0    https://cdn.shopify.com/s/files/1/2364/4077/pr...         $48.99  
1    https://cdn.shopify.com/s/files/1/2364/4077/pr...        $130.99  
2    https://cdn.shopify.com/s/files/1/2364/4077/pr...        $171.99  
3    https://cdn.shopify.com/s/files/1/2364/4077/pr...        $171.99  
4    https://cdn.shopify.com/s/files/1/2364/4077/pr...         $61.99  
..                                                 ...            ...  
711  https://cdn.shopify.com/s/files/1/2364/4077/pr...  $29.99,$37.99  
712  https://cdn.shopify.com/s/files/1/2364/4077/pr...  $48.99,$60.99  
713  https://cdn.shopify.com/s/files/1/2364/4077/pr...        $151.99  
714  https://cdn.shopify.com/s/files/1/2364/4077/pr...         $90.99  
715  https://cdn.shopify.com/s/files/1/2364/4077/pr...  $41.99,$54.99  

[716 rows x 4 columns]

In [9]:
products_woman['product_url'][0]

'https://knowtheorigin.com/products/copy-of-topanga-recycled-pet-bra-plum'

In [199]:
def get_products(df):
    product_material = []
    size = []
    description = []
    brand = []
    secondhand = []
    scrapped_date = []
    for i in range(len(df)):
        m,s,d,b,sh,date=get_details(df['product_url'][i])
        product_material.append(m)
        size.append(s)
        description.append(d)
        brand.append(b)
        secondhand.append(sh)
        scrapped_date.append(date)
    df['product_material']=product_material
    df['size']=size
    df['description']=description
    df['brand_name']=brand
    df['secondhand']=secondhand
    df['scrapped_date']=scrapped_date
    
    return df

In [248]:
def get_details(product_link):
    page = BeautifulSoup(requests.get(product_link).content,'lxml')
    
    
    # Retrieve description
    description = ''
    try:
        des = page.find('div',class_="tab description").find_all('p')
        for item in des:
            line = item.get_text().strip()
            description += line
    except:
        pass
    if not description:
        try:
            description = page.find('div',class_="tab product-description").find_all('p')[0].get_text()
        except:
            pass
    if not description:
        try:
            description = page.find('div',class_="tab description").find('span').get_text()
        except:
            pass
    if not description:
        try:
            description = page.find('div',class_="tab product-description").find_all('p')[0].get_text()
        except:
            pass
    if not description:
        try:
            description = page.find('div',class_='tab description').get_text().strip()
        except:
            pass
    
    materials = []
    # Retrieve product materials
    try:
        # Retreive from "materials" tab if the tab exists
        details = page.find('div',class_='tab materials').find('div').get_text()
        materials = details
    except:
        try:
            # Retrieve from the last line of the "description" tab if there is no "materials" tab
            details = page.find('div',class_='tab description').find_all('p')
            for item in details:
                mat = item.get_text()
                if "%" in mat:
                    materials = mat
                else:
                    # get materials from product name
                    pass
        except:
            # Retrieve from the last line of the "product-description" tab if there is no "description" tab either
            try:
                details = page.find('div',class_="tab product-description").find_all('p')
                for item in details:
                    mat = item.get_text()
                    if "%" in mat:
                        materials = mat
                    else:
                        pass
                        # get materials from product name
            except:
                pass
    if not materials:
        try:
            materials = page.find('div',class_='tab material').get_text().strip()
        except:
            pass
    if not materials:
        try:
            lines = page.find('div',class_='tab description').find('span').get_text().split('> ')
            for l in lines:
                if '%' in l:
                    materials = l
        except:
            pass
    if not materials:
        try:
            lines = page.find('div',class_='tab product-description').find('span').get_text().split('> ')
            for l in lines:
                if '%' in l:
                    materials = l
        except:
            pass
    if not materials:
        try:
            lines = page11.find('div',class_='tab description').get_text().strip().split('\xa0')
            for l in lines:
                if '%' in l:
                    materials = l
        except:
            pass
    if not materials:
        materials = description
            
            
    # Retrieve color from product name
    
    # Retrieve sizes
    size = []
    try:
        size_class = page.find('div',class_="swatch swatch-size clearfix").find_all('label')
        for item in size_class:
            s=item.get_text().strip()
            size.append(s)
        size = json.dumps(size)
    except:
        pass
    
        
    # Second hand
    secondhand='No'
    
    # Brand name
    brand = 'KnowtheOrigin'
    
    # Scrapped date
    date = datetime.today().strftime('%Y-%m-%d')
        
    return materials,size,description,brand,secondhand,date

In [249]:
df = get_products(products_woman)

In [250]:
df

display_name  \
0                        Topanga Recycled PET Bra Plum   
1                Flora Organic Cotton Check Dress Navy   
2          Modelo 89' Recycled Vegan Trainer Off White   
3      Modelo 89' Recycled Vegan Trainer Beige & White   
4                Handy 100% Recycled PET Backpack Rust   
5                Handy 100% Recycled PET Backpack Pink   
6               Handy 100% Recycled PET Backpack Lilac   
7          Juliette Organic Cotton Checked Shirt Brown   
8           Joy Organic Cotton Corduroy Dungarees Lion   
9                  360° PET Sherpa Unisex Jacket Black   
10                         Hera Knitted Sweater Orange   
11                    WUKA Basics Hipster Period Pants   
12                  Modelo 89' Trainer Green and White   
13                  Modelo 89' Trainer Beige and White   
14              Hallie Wildflower Organic Cotton Dress   
15             Modelo 89' Recycled Vegan Trainer White   
16   Choose Love X KTO - Fairtrade Organic Cotton T...   
17   Recycled PET High-Rise Compressive Pocket Legg...   
18                Eva Organic Bamboo G-String Charcoal   
19                     Stella Mauve Low Cut Bamboo Bra   
20              Frankie Organic Bamboo Flares Charcoal   
21                     Stella Olive Low Cut Bamboo Bra   
22                      Kata Organic Cotton Dress Navy   
23   WUKA Organic Cotton Bikini Period Pants - Medi...   
24   Float Seamless Lightweight Recycled PET High-R...   
25   Float Seamless Lightweight Recycled PET High-R...   
26                       Erin Woven Hemp Jumpsuit Navy   
27                  Stella Charcoal Low Cut Bamboo Bra   
28                              Lodi Modal Dress Black   
29   Côte Des Basques Recycled Sustainable Sunglass...   
30         Priti Organic Cotton Cross Back Dress Black   
31               Leonie Organic Cotton Dress Off White   
32              Leo Organic Bamboo High-Cut Bra Cherry   
33   Cleo Float Seamless Lightweight Recycled PET S...   
34                        Sunny Side Modal Dress Black   
35        Classic Organic Cotton T-Shirt Optical White   
36                 Ana Organic Cotton Knit Pants Black   
37      Modelo 89' Recycled Vegan Trainer Grey & White   
38             Essential Organic Cotton Black Leggings   
39             Aidin Hemp Loose Fit T-Shirt Dark Green   
40             Recycled PET High-Rise Bike Short Black   
41                       Paloma Recycled PET Bra Black   
42   Float Seamless Lightweight Recycled PET High-R...   
43   Cleo Float Seamless Lightweight Recycled PET S...   
44                Evelyn Organic Cotton Black Jumpsuit   
45                              Orli Modal Dress Black   
46            Laila Organic Cotton Roll Neck Black Top   
47                  Eva Organic Bamboo G-String Cherry   
48                                  Bumi Leotard Black   
49                    Med Organic Cotton T-Shirt Black   
50             Revi Organic Cotton Hoodie Pacific Blue   
51           Organic Cotton Green Elephant Pants Olive   
52   Sophie Organic & Recycled Cotton Rocks Dip Den...   
53        WUKA Ultimate Tencel Midi Brief Period Pants   
54   Float Seamless Lightweight Recycled PET High-R...   
55   Float Seamless Lightweight Recycled PET High-R...   
56   Juliet Float Seamless Lightweight Recycled PET...   
57                        Paloma Recycled PET Bra Plum   
58   Sona Organic Cotton Heavy Knit Jumper Grey Mel...   
59          Classic Organic Cotton T-Shirt Soft Yellow   
60          Classic Organic Cotton T-Shirt Dusty Olive   
61         Vik Recycled Sustainable Sunglasses Leopard   
62                  Wide Leg Linen Trousers Terracotta   
63                          Birch Linen Cami Top Black   
64             Eva Organic Bamboo G-String Powder Blue   
65            Leo Organic Bamboo High-Cut Bra Charcoal   
66               Leo Organic Bamboo High-Cut Bra Ivory   
67                     Stella Ivory Low Cut Bamboo Bra   
68                    Rainer High Neck N

In [27]:
import psycopg2
import pandas as pd
import numpy as np
import re
import datetime as dt

In [28]:
GranCat = pd.read_csv("LowLevelCatagoryRegex.csv", header=None, skiprows=[0])

def process_cat(df):
    # get all the values in category regex
    subCats = GranCat.iloc[:, 1:]
    Cats = []
    for index, row in subCats.iterrows():
        for i in GranCat.columns[1:]:
            if pd.isnull(row[i]): continue
            else: Cats.append(row[i])
               
    # assign potential category for each clothing row based on title, else other
    clothesCat = []
    for index, row in df.iterrows():
        rowCat = float("NaN")
        for cat in Cats:
            if re.search(cat, row['display_name'].lower()):
                rowCat = cat
                print(rowCat)
                break
        if pd.isnull(rowCat):
            clothesCat.append('other')
        else:
            clothesCat.append(rowCat)

    return clothesCat

# set parent category to each product
def get_cat(x):
    if x == 'other': return x
    else: return [GranCat[0][i] for i in GranCat.index if x in GranCat.iloc[i].to_list()][0]

# get low_level column given a df
def get_lowlevel(df):
    df['low_level_new'] = process_cat(df)
    df['low_level_new'] = df['low_level_new'].apply(lambda x: get_cat(x))
    return df

In [251]:
df = get_lowlevel(df)

bra
dresse?s?
trainers?
trainers?
backpacks?
backpacks?
backpacks?
shirts?
jackets?
sweaters?
pants?
trainers?
trainers?
dresse?s?$
trainers?
t-?shirts?
[jl]eggings?
rings?
bras?$
flares?
bras?$
dresse?s?
pants?
[jl]eggings?
jumpsuits?
bras?$
dresse?s?
basque
dresse?s?
dresse?s?
bra
bra
dresse?s?
t-?shirts?
pants?
trainers?
[jl]eggings?
t-?shirts?
bra
[jl]eggings?
bra
jumpsuits?
dresse?s?
tops?
rings?
leotards?
t-?shirts?
hoodies?
pants?
sk[io]rts?
pants?
bra
bra
knits?
t-?shirts?
t-?shirts?
glasses
trousers?
cami
rings?
bra
bra
bras?$
tops?
[jl]eggings?
bra
bra
tops?
dresse?s?
t-?shirts?
bikinis? ?-?top
dresse?s?$
trainers?
t-?shirts?
t-?shirts?
[jl]eggings?
pants?
dresse?s?
bras?$
trousers?
jeans
socks
bras?$
bandeau
bra
rings?
bra
t-?shirts?
t-?shirts?
bra
jeans
sk[io]rts?
bra
tops?
tops?
bra
bra
bra
t-?shirts?
tops?
t-?shirts?
glasses
bras?$
bras?$
shirts?
dresse?s?$
jumpsuits?
t-?shirts?
glasses
bandeau
pants?
jumpsuits?
trainers?
[jl]eggings?
socks
bra
bra
sk[io]rts?
dresse?s?
sk

In [252]:
df[['display_name','low_level_new']]

display_name  \
0                        Topanga Recycled PET Bra Plum   
1                Flora Organic Cotton Check Dress Navy   
2          Modelo 89' Recycled Vegan Trainer Off White   
3      Modelo 89' Recycled Vegan Trainer Beige & White   
4                Handy 100% Recycled PET Backpack Rust   
5                Handy 100% Recycled PET Backpack Pink   
6               Handy 100% Recycled PET Backpack Lilac   
7          Juliette Organic Cotton Checked Shirt Brown   
8           Joy Organic Cotton Corduroy Dungarees Lion   
9                  360° PET Sherpa Unisex Jacket Black   
10                         Hera Knitted Sweater Orange   
11                    WUKA Basics Hipster Period Pants   
12                  Modelo 89' Trainer Green and White   
13                  Modelo 89' Trainer Beige and White   
14              Hallie Wildflower Organic Cotton Dress   
15             Modelo 89' Recycled Vegan Trainer White   
16   Choose Love X KTO - Fairtrade Organic Cotton T...   
17   Recycled PET High-Rise Compressive Pocket Legg...   
18                Eva Organic Bamboo G-String Charcoal   
19                     Stella Mauve Low Cut Bamboo Bra   
20              Frankie Organic Bamboo Flares Charcoal   
21                     Stella Olive Low Cut Bamboo Bra   
22                      Kata Organic Cotton Dress Navy   
23   WUKA Organic Cotton Bikini Period Pants - Medi...   
24   Float Seamless Lightweight Recycled PET High-R...   
25   Float Seamless Lightweight Recycled PET High-R...   
26                       Erin Woven Hemp Jumpsuit Navy   
27                  Stella Charcoal Low Cut Bamboo Bra   
28                              Lodi Modal Dress Black   
29   Côte Des Basques Recycled Sustainable Sunglass...   
30         Priti Organic Cotton Cross Back Dress Black   
31               Leonie Organic Cotton Dress Off White   
32              Leo Organic Bamboo High-Cut Bra Cherry   
33   Cleo Float Seamless Lightweight Recycled PET S...   
34                        Sunny Side Modal Dress Black   
35        Classic Organic Cotton T-Shirt Optical White   
36                 Ana Organic Cotton Knit Pants Black   
37      Modelo 89' Recycled Vegan Trainer Grey & White   
38             Essential Organic Cotton Black Leggings   
39             Aidin Hemp Loose Fit T-Shirt Dark Green   
40             Recycled PET High-Rise Bike Short Black   
41                       Paloma Recycled PET Bra Black   
42   Float Seamless Lightweight Recycled PET High-R...   
43   Cleo Float Seamless Lightweight Recycled PET S...   
44                Evelyn Organic Cotton Black Jumpsuit   
45                              Orli Modal Dress Black   
46            Laila Organic Cotton Roll Neck Black Top   
47                  Eva Organic Bamboo G-String Cherry   
48                                  Bumi Leotard Black   
49                    Med Organic Cotton T-Shirt Black   
50             Revi Organic Cotton Hoodie Pacific Blue   
51           Organic Cotton Green Elephant Pants Olive   
52   Sophie Organic & Recycled Cotton Rocks Dip Den...   
53        WUKA Ultimate Tencel Midi Brief Period Pants   
54   Float Seamless Lightweight Recycled PET High-R...   
55   Float Seamless Lightweight Recycled PET High-R...   
56   Juliet Float Seamless Lightweight Recycled PET...   
57                        Paloma Recycled PET Bra Plum   
58   Sona Organic Cotton Heavy Knit Jumper Grey Mel...   
59          Classic Organic Cotton T-Shirt Soft Yellow   
60          Classic Organic Cotton T-Shirt Dusty Olive   
61         Vik Recycled Sustainable Sunglasses Leopard   
62                  Wide Leg Linen Trousers Terracotta   
63                          Birch Linen Cami Top Black   
64             Eva Organic Bamboo G-String Powder Blue   
65            Leo Organic Bamboo High-Cut Bra Charcoal   
66               Leo Organic Bamboo High-Cut Bra Ivory   
67                     Stella Ivory Low Cut Bamboo Bra   
68                    Rainer High Neck N

In [253]:
df[df['low_level_new']=='other'][['display_name','low_level_new']]

display_name low_level_new
8           Joy Organic Cotton Corduroy Dungarees Lion         other
25   Float Seamless Lightweight Recycled PET High-R...         other
40             Recycled PET High-Rise Bike Short Black         other
54   Float Seamless Lightweight Recycled PET High-R...         other
55   Float Seamless Lightweight Recycled PET High-R...         other
88         Maya Organic Bamboo Low-Waist Undies Cherry         other
92                  Maya Olive Low Waist Bamboo Undies         other
93        Lena Organic Bamboo High-Waisted Undies Pink         other
94       Lena Organic Bamboo High-Waisted Undies Olive         other
100               White Granite Hexagonal Trinket Dish         other
117                       Better Together Jumper Black         other
120                      Organic Cotton Dungarees Pink         other
122     Lena Organic Bamboo High-Waisted Undies Cherry         other
123           Maya Powder Blue Low Waist Bamboo Undies         other
124   Lena Organic Bamboo High-Waisted Undies Charcoal         other
133                     Organic Cotton Pyjama Set Navy         other
135                     Organic Cotton Pyjama Set Pink         other
140  Mary Lou Organic Linen & Cotton Mix Dungarees ...         other
142                      Organic Cotton Dungarees Blue         other
145         Joy Organic Cotton Corduroy Dungarees Pine         other
147                     Organic Cotton Dungarees Black         other
153      Maya Organic Bamboo Low-Waist Undies Charcoal         other
165  Float Seamless Lightweight Recycled PET High-R...         other
168                    Organic Cotton Pyjama Set Wheat         other
169                    Organic Cotton Pyjama Set White         other
181      Lena Organic Bamboo High-Waisted Undies Mauve         other
182  Lena Organic Bamboo High-Waisted Undies Powder...         other
184                   Kesh Organic Cotton Jumper Black         other
192             Recycled PET High-Rise Bike Short Plum         other
221         Recycled PET High-rise Bike Short Midnight         other
226                     Brooklyn Twill Dungarees Ivory         other
230                 Pink Marble Hexagonal Trinket Dish         other
247         Recycled PET High-Rise Bike Short Geranium         other
267     Venus Organic Cotton Corduroy Overall Clay Red         other
270  Bobbie Surplus Fabric Cotton Twill Suit Baby Pink         other
271  Joni Surplus Fabric Cotton Twill Playsuit Sky ...         other
272  Zebina Pla And Bamboo Coffee Cup And Sock Gift...         other
280      100% Bamboo Under My Umbrella Pyjama Set Pink         other
285          Recycled PET High-Rise Bike Short Monarch         other
286             Recycled PET High-Rise Bike Short Haze         other
287        Recycled PET High-Rise Bike Short Limestone         other
295              Ashton Surplus Fabric Linen Suit Blue         other
309           Recycled PET High-Rise Bike Short Quartz         other
310      Recycled PET High-Rise Bike Short Chartreuses         other
311             Recycled PET High-Rise Bike Short Tart         other
313         Recycled PET High-Rise Bike Short Sky Blue         other
319           Joy Organic Cotton Dungarees Navy Stripe         other
335  Mary Lou Organic Linen & Cotton Mix Dungarees ...         other
336  Mary Lou Organic Linen & Cotton Mix Dungarees ...         other
337  Mary Lou Organic Linen & Cotton Mix Dungarees ...         other
338      Lena Organic Bamboo High-Waisted Undies Ivory         other
396      Russian Circle Recycled Sterling Silver Studs         other
402                      Recycled 9ct Gold Pearl Hoops         other
441        Loren Organic Cotton & Wool Ruby Red Jumper         other
456  Henley Surplus Fabric Cotton Twill Suit Dark Navy         other
457      Bobbie Surplus Fabric Cotton Twill Suit Lilac         other
475         Maya Organic Bamboo Low-Waist Undies Ivory         other
488         Loka Recycled Silver Twisted

In [254]:
df=df.drop(['low_level'], axis=1)

KeyError: "['low_level'] not found in axis"

In [255]:
df = df.rename(columns={"low_level_new": "low_level"})

In [257]:
def get_id(df, date='20211021'):
    brand = df['brand_name'][0]
    clothing_ids = []
    for i in range(len(df.index)):
        clothing_id = date + brand + str(i)
        clothing_ids.append(clothing_id)
    return clothing_ids

In [258]:
df['clothing_id'] = get_id(df)

In [259]:
df = df.set_index('clothing_id')

In [260]:
df['gender']='Women'

In [262]:
name_list = df['display_name'].values.tolist()

In [55]:
name_list

['Topanga Recycled PET Bra Plum',
 'Flora Organic Cotton Check Dress Navy',
 "Modelo 89' Recycled Vegan Trainer Off White",
 "Modelo 89' Recycled Vegan Trainer Beige & White",
 'Handy 100% Recycled PET Backpack Rust',
 'Handy 100% Recycled PET Backpack Pink',
 'Handy 100% Recycled PET Backpack Lilac',
 'Juliette Organic Cotton Checked Shirt Brown',
 'Joy Organic Cotton Corduroy Dungarees Lion',
 '360° PET Sherpa Unisex Jacket Black',
 'Hera Knitted Sweater Orange',
 'WUKA Basics Hipster Period Pants',
 "Modelo 89' Trainer Green and White",
 "Modelo 89' Trainer Beige and White",
 'Hallie Wildflower Organic Cotton Dress',
 "Modelo 89' Recycled Vegan Trainer White",
 'Choose Love X KTO - Fairtrade Organic Cotton T-Shirt Grey',
 'Recycled PET High-Rise Compressive Pocket Leggings Black',
 'Eva Organic Bamboo G-String Charcoal',
 'Stella Mauve Low Cut Bamboo Bra',
 'Frankie Organic Bamboo Flares Charcoal',
 'Stella Olive Low Cut Bamboo Bra',
 'Kata Organic Cotton Dress Navy',
 'WUKA Organic

In [263]:
color_single = []
for item in name_list:
    try:
        color1 = item.split(' ')[-1]
    except:
        pass
    color_single.append(color1) if color1 not in color_single else color_single

In [72]:
color_single

['Plum',
 'Navy',
 'White',
 'Rust',
 'Pink',
 'Lilac',
 'Brown',
 'Lion',
 'Black',
 'Orange',
 'Pants',
 'Dress',
 'Grey',
 'Charcoal',
 'Bra',
 'Flow',
 'Leopard',
 'Cherry',
 'Leggings',
 'Green',
 'Midnight',
 'Jumpsuit',
 'Top',
 'Blue',
 'Olive',
 'Fern',
 'Melange',
 'Yellow',
 'Terracotta',
 'Ivory',
 'Fig',
 'Eucalyptus',
 'Jeans',
 'Socks',
 'Undies',
 'Pumpkin',
 'Dish',
 'Red',
 'Horizon',
 'Stripe',
 'Soles',
 'Geranium',
 'Dungarees',
 'Skirt',
 'Floral',
 'Oat',
 'Pine',
 'Mustard',
 'Unitard',
 'Denim',
 'Vermeil',
 'Wheat',
 'Indigo',
 'Camel',
 'Mauve',
 'Malange',
 'Stripes',
 'Ecru',
 'Beige',
 'Oatmeal',
 'Silver',
 'Monarch',
 'Raspberry',
 'Sock',
 'Shorts',
 'Bralette',
 'Trousers',
 'Burgundy',
 'Tart',
 'Band',
 'Greige',
 'Set',
 'Mint',
 'Trouser',
 'Asphalt',
 'Stitch',
 'Honey',
 'Gingham',
 'Box',
 'Haze',
 'Limestone',
 'T-Shirt',
 'Lime',
 'Quartz',
 'Chartreuses',
 'Natural',
 'Gold',
 'Necklace',
 'Khaki',
 'Stone',
 'Hoops',
 'Sage',
 'Ring',
 'Lave

In [264]:
color_double = []
for item in name_list:
    try:
        color2 = item.split(' ')[-2]+' '+item.split(' ')[-1]
    except:
        pass
    color_double.append(color2) if color2 not in color_double else color_double

In [78]:
color_double

['Bra Plum',
 'Dress Navy',
 'Off White',
 '& White',
 'Backpack Rust',
 'Backpack Pink',
 'Backpack Lilac',
 'Shirt Brown',
 'Dungarees Lion',
 'Jacket Black',
 'Sweater Orange',
 'Period Pants',
 'and White',
 'Cotton Dress',
 'Trainer White',
 'T-Shirt Grey',
 'Leggings Black',
 'G-String Charcoal',
 'Bamboo Bra',
 'Flares Charcoal',
 'Medium Flow',
 'Short Black',
 'Jumpsuit Navy',
 'Dress Black',
 'Sunglasses Leopard',
 'Bra Cherry',
 'Bra Black',
 'Optical White',
 'Pants Black',
 'Black Leggings',
 'Dark Green',
 'Leggings Midnight',
 'Bra Midnight',
 'Black Jumpsuit',
 'Black Top',
 'G-String Cherry',
 'Leotard Black',
 'T-Shirt Black',
 'Pacific Blue',
 'Pants Olive',
 'Skirt Black',
 'Short Midnight',
 'Short Fern',
 'Grey Melange',
 'Soft Yellow',
 'Dusty Olive',
 'Trousers Terracotta',
 'Top Black',
 'Powder Blue',
 'Bra Charcoal',
 'Bra Ivory',
 'Stripe Top',
 'Leggings Plum',
 'Bra Fig',
 'T-Shirt Navy',
 'Blue Eucalyptus',
 'Summer Dress',
 'Trainer Black',
 'Stone Blue'

In [265]:
color_triple = []
for item in name_list:
    try:
        color3 = item.split(' ')[-3]+' '+item.split(' ')[-2]+' '+item.split(' ')[-1]
    except:
        pass
    color_triple.append(color3) if color3 not in color_triple else color_triple

In [117]:
color_triple[580:600]

[]

In [266]:
color1 = []
for i in color_single:
    if i not in ('Lion','Pants','Dress','Bra','Flow','Leggings','Jumpsuit','Top','Jeans','Socks','Undies','Dish','Soles',
                'Dungarees','Skirt','Unitard','Denim','Socks','Shorts','Bralette','Trousers','Band', 'Set','Trouser',
                'Stitch','Box','T-Shirt','Necklace','Stone','Hoops','Ring','Studs','Earrings','Vest','Cardigam',
                'Blouse','Plated','Jumper','Tights','Bundle','Bag','Café','Pack','Bar','Cufflinks','Kit','Hoodie','Jacket',
                'Ripple','Duster','Cuff','Bracelet','Wristband','Backpack','Knit','Boilersuit','Leotard'):
        color1.append(i)

In [267]:
color2 = []
color2.extend(['Off White','Optical White','Dark Green','Pacific Blue','Grey Melange','Dusty Olive','Powder Blue',
             'Blue Eucalyptus','Stone Blue','Faded Pink','Dark Blue','Pastel Yellow','Heather Grey','Light Sage','Pastel Pink',
            'Soft Lavender','Bright White','Dark Sand','Orange Papaya','Dark Navy','Glacier Grey','Pine Green','Rose Gold',
            'Misty Lilac','Dark Grey','Dark Charcoal','Light Grey','Desert Khaki','Dark Mint','Light Sage','Light Blue',
               'Sea Pink','Rose Grey','Ombre Blue','Navy Tartan','Sky Blue'])

In [268]:
color3 = []
color3.extend(['Beige & White','Green and White','Beige and White','Grey & White','Black & White','Navy & White',
               'Red and White','Navy and White'])

In [269]:
len(color1)

82

In [270]:
df['color']=''

In [271]:
for i in range(len(df)):
    c = ''
    try:
        for x in color3:
                if x in df['display_name'][i]:
                    c = x
                    break
                else:
                    for y in color2:
                        if y in df['display_name'][i]:
                            c = y 
                            break
                        else:
                            for z in color1:
                                if z in df['display_name'][i]:
                                    c = z
    except:
        pass
    df['color_new'][i] = c

In [272]:
df['image_color_link_new'] = ''

In [273]:
for i in range(len(df)):
    df['image_color_link_new'][i] = {df['color'][i]:df['image_color_link'][i]}

In [274]:
df.drop(['image_color_link'], axis=1)

display_name  \
clothing_id                                                                   
20211021KnowtheOrigin0                        Topanga Recycled PET Bra Plum   
20211021KnowtheOrigin1                Flora Organic Cotton Check Dress Navy   
20211021KnowtheOrigin2          Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin3      Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin4                Handy 100% Recycled PET Backpack Rust   
20211021KnowtheOrigin5                Handy 100% Recycled PET Backpack Pink   
20211021KnowtheOrigin6               Handy 100% Recycled PET Backpack Lilac   
20211021KnowtheOrigin7          Juliette Organic Cotton Checked Shirt Brown   
20211021KnowtheOrigin8           Joy Organic Cotton Corduroy Dungarees Lion   
20211021KnowtheOrigin9                  360° PET Sherpa Unisex Jacket Black   
20211021KnowtheOrigin10                         Hera Knitted Sweater Orange   
20211021KnowtheOrigin11                    WUKA Basics Hipster Period Pants   
20211021KnowtheOrigin12                  Modelo 89' Trainer Green and White   
20211021KnowtheOrigin13                  Modelo 89' Trainer Beige and White   
20211021KnowtheOrigin14              Hallie Wildflower Organic Cotton Dress   
20211021KnowtheOrigin15             Modelo 89' Recycled Vegan Trainer White   
20211021KnowtheOrigin16   Choose Love X KTO - Fairtrade Organic Cotton T...   
20211021KnowtheOrigin17   Recycled PET High-Rise Compressive Pocket Legg...   
20211021KnowtheOrigin18                Eva Organic Bamboo G-String Charcoal   
20211021KnowtheOrigin19                     Stella Mauve Low Cut Bamboo Bra   
20211021KnowtheOrigin20              Frankie Organic Bamboo Flares Charcoal   
20211021KnowtheOrigin21                     Stella Olive Low Cut Bamboo Bra   
20211021KnowtheOrigin22                      Kata Organic Cotton Dress Navy   
20211021KnowtheOrigin23   WUKA Organic Cotton Bikini Period Pants - Medi...   
20211021KnowtheOrigin24   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin25   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin26                       Erin Woven Hemp Jumpsuit Navy   
20211021KnowtheOrigin27                  Stella Charcoal Low Cut Bamboo Bra   
20211021KnowtheOrigin28                              Lodi Modal Dress Black   
20211021KnowtheOrigin29   Côte Des Basques Recycled Sustainable Sunglass...   
20211021KnowtheOrigin30         Priti Organic Cotton Cross Back Dress Black   
20211021KnowtheOrigin31               Leonie Organic Cotton Dress Off White   
20211021KnowtheOrigin32              Leo Organic Bamboo High-Cut Bra Cherry   
20211021KnowtheOrigin33   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin34                        Sunny Side Modal Dress Black   
20211021KnowtheOrigin35        Classic Organic Cotton T-Shirt Optical White   
20211021KnowtheOrigin36                 Ana Organic Cotton Knit Pants Black   
20211021KnowtheOrigin37      Modelo 89' Recycled Vegan Trainer Grey & White   
20211021KnowtheOrigin38             Essential Organic Cotton Black Leggings   
20211021KnowtheOrigin39             Aidin Hemp Loose Fit T-Shirt Dark Green   
20211021KnowtheOrigin40             Recycled PET High-Rise Bike Short Black   
20211021KnowtheOrigin41                       Paloma Recycled PET Bra Black   
20211021KnowtheOrigin42   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin43   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin44                Evelyn Organic Cotton Black Jumpsuit   
20211021KnowtheOrigin45                              Orli Modal Dress Black   
20211021KnowtheOrigin46            Laila Organic Cotton Roll Neck Black Top   
20211021KnowtheOrigin47                  Eva Organic Bamboo G-String Cherry   
20211021KnowtheOrigin48                                  Bumi Leotard Black   
20211021KnowtheOrigin49           

In [280]:
df = df.rename(columns={'image_color_link_new': 'image_color_link'})

In [281]:
df = df.rename(columns={'image_color_link': 'image_link_color'})

In [282]:
df

display_name  \
clothing_id                                                                   
20211021KnowtheOrigin0                        Topanga Recycled PET Bra Plum   
20211021KnowtheOrigin1                Flora Organic Cotton Check Dress Navy   
20211021KnowtheOrigin2          Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin3      Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin4                Handy 100% Recycled PET Backpack Rust   
20211021KnowtheOrigin5                Handy 100% Recycled PET Backpack Pink   
20211021KnowtheOrigin6               Handy 100% Recycled PET Backpack Lilac   
20211021KnowtheOrigin7          Juliette Organic Cotton Checked Shirt Brown   
20211021KnowtheOrigin8           Joy Organic Cotton Corduroy Dungarees Lion   
20211021KnowtheOrigin9                  360° PET Sherpa Unisex Jacket Black   
20211021KnowtheOrigin10                         Hera Knitted Sweater Orange   
20211021KnowtheOrigin11                    WUKA Basics Hipster Period Pants   
20211021KnowtheOrigin12                  Modelo 89' Trainer Green and White   
20211021KnowtheOrigin13                  Modelo 89' Trainer Beige and White   
20211021KnowtheOrigin14              Hallie Wildflower Organic Cotton Dress   
20211021KnowtheOrigin15             Modelo 89' Recycled Vegan Trainer White   
20211021KnowtheOrigin16   Choose Love X KTO - Fairtrade Organic Cotton T...   
20211021KnowtheOrigin17   Recycled PET High-Rise Compressive Pocket Legg...   
20211021KnowtheOrigin18                Eva Organic Bamboo G-String Charcoal   
20211021KnowtheOrigin19                     Stella Mauve Low Cut Bamboo Bra   
20211021KnowtheOrigin20              Frankie Organic Bamboo Flares Charcoal   
20211021KnowtheOrigin21                     Stella Olive Low Cut Bamboo Bra   
20211021KnowtheOrigin22                      Kata Organic Cotton Dress Navy   
20211021KnowtheOrigin23   WUKA Organic Cotton Bikini Period Pants - Medi...   
20211021KnowtheOrigin24   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin25   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin26                       Erin Woven Hemp Jumpsuit Navy   
20211021KnowtheOrigin27                  Stella Charcoal Low Cut Bamboo Bra   
20211021KnowtheOrigin28                              Lodi Modal Dress Black   
20211021KnowtheOrigin29   Côte Des Basques Recycled Sustainable Sunglass...   
20211021KnowtheOrigin30         Priti Organic Cotton Cross Back Dress Black   
20211021KnowtheOrigin31               Leonie Organic Cotton Dress Off White   
20211021KnowtheOrigin32              Leo Organic Bamboo High-Cut Bra Cherry   
20211021KnowtheOrigin33   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin34                        Sunny Side Modal Dress Black   
20211021KnowtheOrigin35        Classic Organic Cotton T-Shirt Optical White   
20211021KnowtheOrigin36                 Ana Organic Cotton Knit Pants Black   
20211021KnowtheOrigin37      Modelo 89' Recycled Vegan Trainer Grey & White   
20211021KnowtheOrigin38             Essential Organic Cotton Black Leggings   
20211021KnowtheOrigin39             Aidin Hemp Loose Fit T-Shirt Dark Green   
20211021KnowtheOrigin40             Recycled PET High-Rise Bike Short Black   
20211021KnowtheOrigin41                       Paloma Recycled PET Bra Black   
20211021KnowtheOrigin42   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin43   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin44                Evelyn Organic Cotton Black Jumpsuit   
20211021KnowtheOrigin45                              Orli Modal Dress Black   
20211021KnowtheOrigin46            Laila Organic Cotton Roll Neck Black Top   
20211021KnowtheOrigin47                  Eva Organic Bamboo G-String Cherry   
20211021KnowtheOrigin48                                  Bumi Leotard Black   
20211021KnowtheOrigin49           

In [283]:
products_man = pd.read_csv('kto_men.csv')

In [284]:
products_man = products_man.drop(['item-vendor'],axis=1)

In [285]:
products_man 

display_name  \
0                       Ecru Organic Cotton Sweatshirt   
1          #3001 Organic Cotton Button Overshirt Khaki   
2           #3003 Organic Cotton Button Overshirt Navy   
3      #5005 Organic Cotton Workwear Pants Faded Black   
4              Heavyweight Organic Cotton T-shirt Bark   
5                     Organic Cotton Oxford Shirt Blue   
6                    Organic Cotton Boxers 2-Pack Grey   
7                  Organic Cotton T-Shirt Navy Striped   
8    Regular Dunn Organic & Recycled Cotton Black J...   
9                 SilverTech Active White Tennis Socks   
10                    Rovigo Organic Cotton Navy Shirt   
11   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
12   Clean Clothes Campaign X KTO - Fairtrade Organ...   
13   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
14    Heavyweight Organic Cotton T-shirt Blue Graphite   
15               Emanuele Organic Cotton Navy Trousers   
16   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
17            Heavyweight Organic Cotton T-shirt White   
18                     Arthur Bamboo Boxer Shorts Grey   
19            Organic Cotton Flannel Shirt Pale Yellow   
20                  Organic Cotton Sweatshirt Burgundy   
21           #5005 Organic Cotton Workwear Pants Khaki   
22          Organic Cotton Short Sleeved T-Shirt White   
23              Emanuele Organic Cotton Trousers Khaki   
24    Bes Microcorduroy Organic Cotton Overshirt Camel   
25                             Mark Jacket Olive Green   
26   Finley Gots Cotton Boxer & Sock Gift Box (6 Pack)   
27                     Mark Organic Cotton Jacket Navy   
28     Modelo 89' Recycled Vegan Trainer Beige & White   
29         Modelo 89' Recycled Vegan Trainer Off White   
30             Modelo 89' Recycled Vegan Trainer White   
31   Choose Love X KTO - Fairtrade Organic Cotton T...   
32   Mind X KTO - Fairtrade Organic Cotton T-Shirt ...   
33               Kopfkino Organic Cotton T-Shirt Black   
34   Côte Des Basques Recycled Sustainable Sunglass...   
35      Modelo 89' Recycled Vegan Trainer Grey & White   
36                 Basic Crew Neck Lambswool Knit Blue   
37   Barnabus X KTO - Fairtrade Organic Cotton T-Sh...   
38        Classic Organic Cotton T-Shirt Optical White   
39        Nicole Recycled Sustainable Sunglasses Black   
40          Abstract Bone Organic Cotton T-Shirt White   
41         Vik Recycled Sustainable Sunglasses Leopard   
42   Regular Bryce Organic & Recycled Cotton Strong...   
43          Classic Organic Cotton T-Shirt Dusty Olive   
44     Organic Cotton Short Sleeved T-Shirt Lily Green   
45          Breda Recycled Polyester Jacket Dark Khaki   
46               Challenge Vegan Leather Trainer Black   
47           Organic Cotton Pink Melange Flannel Shirt   
48                 Basic Crew Neck Lambswool Knit Grey   
49           Vik Recycled Sustainable Sunglasses Black   
50      Nicole Recycled Sustainable Sunglasses Mustard   
51   Vincent Organic Cotton Merino Wool Knitted Pol...   
52   Bes Microcorduroy Organic Cotton Overshirt Cla...   
53                 Mask Organic Cotton Sweatshirt Navy   
54          Organic Cotton Short Sleeved T-Shirt Peach   
55           Classic Organic Cotton T-Shirt Stone Blue   
56                 Marcelino Organic Cotton Pants Navy   
57                   Know The Origin Digital Gift Card   
58                   Travel Organic Cotton Pants Olive   
59         Classic Organic Cotton Sweatpants Navy Blue   
60             Classic Organic Cotton Hoodie Navy Blue   
61          Classic Organic Cotton T-Shirt Soft Yellow   
62                Agra Organic Cotton T-Shirt Burgundy   
63           Classic Organic Cotton T-Shirt Faded Pink   
64                         Teja Hemp T-Shirt Raspberry   
65                     Soloist Trousers Indigo Stripes   
66       Classic Organic Cotton Sweatpants Dusty Olive   
67         Asp Women's Recycled Polyester Jacket Black   
68         Sophie Faux Fur Organic Cotto

In [286]:
df2 = get_products(products_man)

In [287]:
df2

display_name  \
0                       Ecru Organic Cotton Sweatshirt   
1          #3001 Organic Cotton Button Overshirt Khaki   
2           #3003 Organic Cotton Button Overshirt Navy   
3      #5005 Organic Cotton Workwear Pants Faded Black   
4              Heavyweight Organic Cotton T-shirt Bark   
5                     Organic Cotton Oxford Shirt Blue   
6                    Organic Cotton Boxers 2-Pack Grey   
7                  Organic Cotton T-Shirt Navy Striped   
8    Regular Dunn Organic & Recycled Cotton Black J...   
9                 SilverTech Active White Tennis Socks   
10                    Rovigo Organic Cotton Navy Shirt   
11   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
12   Clean Clothes Campaign X KTO - Fairtrade Organ...   
13   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
14    Heavyweight Organic Cotton T-shirt Blue Graphite   
15               Emanuele Organic Cotton Navy Trousers   
16   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
17            Heavyweight Organic Cotton T-shirt White   
18                     Arthur Bamboo Boxer Shorts Grey   
19            Organic Cotton Flannel Shirt Pale Yellow   
20                  Organic Cotton Sweatshirt Burgundy   
21           #5005 Organic Cotton Workwear Pants Khaki   
22          Organic Cotton Short Sleeved T-Shirt White   
23              Emanuele Organic Cotton Trousers Khaki   
24    Bes Microcorduroy Organic Cotton Overshirt Camel   
25                             Mark Jacket Olive Green   
26   Finley Gots Cotton Boxer & Sock Gift Box (6 Pack)   
27                     Mark Organic Cotton Jacket Navy   
28     Modelo 89' Recycled Vegan Trainer Beige & White   
29         Modelo 89' Recycled Vegan Trainer Off White   
30             Modelo 89' Recycled Vegan Trainer White   
31   Choose Love X KTO - Fairtrade Organic Cotton T...   
32   Mind X KTO - Fairtrade Organic Cotton T-Shirt ...   
33               Kopfkino Organic Cotton T-Shirt Black   
34   Côte Des Basques Recycled Sustainable Sunglass...   
35      Modelo 89' Recycled Vegan Trainer Grey & White   
36                 Basic Crew Neck Lambswool Knit Blue   
37   Barnabus X KTO - Fairtrade Organic Cotton T-Sh...   
38        Classic Organic Cotton T-Shirt Optical White   
39        Nicole Recycled Sustainable Sunglasses Black   
40          Abstract Bone Organic Cotton T-Shirt White   
41         Vik Recycled Sustainable Sunglasses Leopard   
42   Regular Bryce Organic & Recycled Cotton Strong...   
43          Classic Organic Cotton T-Shirt Dusty Olive   
44     Organic Cotton Short Sleeved T-Shirt Lily Green   
45          Breda Recycled Polyester Jacket Dark Khaki   
46               Challenge Vegan Leather Trainer Black   
47           Organic Cotton Pink Melange Flannel Shirt   
48                 Basic Crew Neck Lambswool Knit Grey   
49           Vik Recycled Sustainable Sunglasses Black   
50      Nicole Recycled Sustainable Sunglasses Mustard   
51   Vincent Organic Cotton Merino Wool Knitted Pol...   
52   Bes Microcorduroy Organic Cotton Overshirt Cla...   
53                 Mask Organic Cotton Sweatshirt Navy   
54          Organic Cotton Short Sleeved T-Shirt Peach   
55           Classic Organic Cotton T-Shirt Stone Blue   
56                 Marcelino Organic Cotton Pants Navy   
57                   Know The Origin Digital Gift Card   
58                   Travel Organic Cotton Pants Olive   
59         Classic Organic Cotton Sweatpants Navy Blue   
60             Classic Organic Cotton Hoodie Navy Blue   
61          Classic Organic Cotton T-Shirt Soft Yellow   
62                Agra Organic Cotton T-Shirt Burgundy   
63           Classic Organic Cotton T-Shirt Faded Pink   
64                         Teja Hemp T-Shirt Raspberry   
65                     Soloist Trousers Indigo Stripes   
66       Classic Organic Cotton Sweatpants Dusty Olive   
67         Asp Women's Recycled Polyester Jacket Black   
68         Sophie Faux Fur Organic Cotto

In [288]:
df2 = get_lowlevel(df2)

sweatshirts?
shirts?
shirts?
pants?
t-?shirts?
shirts?
boxers?
t-?shirts?
jeans
socks
shirts?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
trousers?
t-?shirts?
t-?shirts?
boxers?
shirts?
sweatshirts?
pants?
t-?shirts?
trousers?
shirts?
jackets?
boxers?
jackets?
trainers?
trainers?
trainers?
t-?shirts?
t-?shirts?
t-?shirts?
basque
trainers?
knits?
t-?shirts?
t-?shirts?
glasses
t-?shirts?
glasses
jeans
t-?shirts?
t-?shirts?
jackets?
trainers?
shirts?
knits?
glasses
glasses
polo
shirts?
sweatshirts?
t-?shirts?
t-?shirts?
pants?
pants?
pants?
hoodies?
t-?shirts?
t-?shirts?
t-?shirts?
t-?shirts?
trousers?
pants?
jackets?
jackets?
t-?shirts?
pants?
shorts
backpacks?
t-?shirts?
socks
shorts
trainers?
t-?shirts?
jackets?
jackets?
jackets?
jackets?
glasses
glasses
boxers?
jackets?
shirts?
shirts?
t-?shirts?
polo
socks
socks
jackets?
jackets?
pants?
glasses
t-?shirts?
t-?shirts?
t-?shirts?
shirts?
t-?shirts?
shirts?
t-?shirts?
jeans
socks
shorts
shorts
t-?shirts?
t-?shirts?
sweatshirts?
sweatshir

In [289]:
df2[df2['low_level_new']=='other'][['display_name','low_level_new']]

display_name low_level_new
57                   Know The Origin Digital Gift Card         other
90   Zebina Pla And Bamboo Coffee Cup And Sock Gift...         other
98                  Know The Origin Physical Gift Card         other
118                         Reilly Cork Card Case Blue         other
162                        Reilly Cork Card Case Brown         other
163                      Reilly Cork Card Case Natural         other

In [290]:
df2=df2.drop(['low_level'], axis=1)

KeyError: "['low_level'] not found in axis"

In [291]:
df2 = df2.rename(columns={"low_level_new": "low_level"})

In [292]:
df2['clothing_id'] = get_id(df2)

In [293]:
df2 = df2.set_index('clothing_id')

In [294]:
df2['gender']='Men'

In [295]:
df2['color']=''

In [296]:
for i in range(len(df2)):
    c = ''
    try:
        for x in color3:
            if x in df2['display_name'][i]:
                c = x
            else:
                raise error
    except:
        try:
            for y in color2:
                if y in df2['display_name'][i]:
                    c = y
                else:
                    raise error
        except:
            for z in color1:
                if z in df2['display_name'][i]:
                    c = z
    df2['color'][i] = c

In [297]:
df2['image_link_color_new'] = ''

In [298]:
for i in range(len(df2)):
    df2['image_link_color_new'][i] = {df2['color'][i]:df2['image_link_color'][i]}

In [299]:
df2.drop(['image_link_color'], axis=1)

display_name  \
clothing_id                                                                   
20211021KnowtheOrigin0                       Ecru Organic Cotton Sweatshirt   
20211021KnowtheOrigin1          #3001 Organic Cotton Button Overshirt Khaki   
20211021KnowtheOrigin2           #3003 Organic Cotton Button Overshirt Navy   
20211021KnowtheOrigin3      #5005 Organic Cotton Workwear Pants Faded Black   
20211021KnowtheOrigin4              Heavyweight Organic Cotton T-shirt Bark   
20211021KnowtheOrigin5                     Organic Cotton Oxford Shirt Blue   
20211021KnowtheOrigin6                    Organic Cotton Boxers 2-Pack Grey   
20211021KnowtheOrigin7                  Organic Cotton T-Shirt Navy Striped   
20211021KnowtheOrigin8    Regular Dunn Organic & Recycled Cotton Black J...   
20211021KnowtheOrigin9                 SilverTech Active White Tennis Socks   
20211021KnowtheOrigin10                    Rovigo Organic Cotton Navy Shirt   
20211021KnowtheOrigin11   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
20211021KnowtheOrigin12   Clean Clothes Campaign X KTO - Fairtrade Organ...   
20211021KnowtheOrigin13   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
20211021KnowtheOrigin14    Heavyweight Organic Cotton T-shirt Blue Graphite   
20211021KnowtheOrigin15               Emanuele Organic Cotton Navy Trousers   
20211021KnowtheOrigin16   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
20211021KnowtheOrigin17            Heavyweight Organic Cotton T-shirt White   
20211021KnowtheOrigin18                     Arthur Bamboo Boxer Shorts Grey   
20211021KnowtheOrigin19            Organic Cotton Flannel Shirt Pale Yellow   
20211021KnowtheOrigin20                  Organic Cotton Sweatshirt Burgundy   
20211021KnowtheOrigin21           #5005 Organic Cotton Workwear Pants Khaki   
20211021KnowtheOrigin22          Organic Cotton Short Sleeved T-Shirt White   
20211021KnowtheOrigin23              Emanuele Organic Cotton Trousers Khaki   
20211021KnowtheOrigin24    Bes Microcorduroy Organic Cotton Overshirt Camel   
20211021KnowtheOrigin25                             Mark Jacket Olive Green   
20211021KnowtheOrigin26   Finley Gots Cotton Boxer & Sock Gift Box (6 Pack)   
20211021KnowtheOrigin27                     Mark Organic Cotton Jacket Navy   
20211021KnowtheOrigin28     Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin29         Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin30             Modelo 89' Recycled Vegan Trainer White   
20211021KnowtheOrigin31   Choose Love X KTO - Fairtrade Organic Cotton T...   
20211021KnowtheOrigin32   Mind X KTO - Fairtrade Organic Cotton T-Shirt ...   
20211021KnowtheOrigin33               Kopfkino Organic Cotton T-Shirt Black   
20211021KnowtheOrigin34   Côte Des Basques Recycled Sustainable Sunglass...   
20211021KnowtheOrigin35      Modelo 89' Recycled Vegan Trainer Grey & White   
20211021KnowtheOrigin36                 Basic Crew Neck Lambswool Knit Blue   
20211021KnowtheOrigin37   Barnabus X KTO - Fairtrade Organic Cotton T-Sh...   
20211021KnowtheOrigin38        Classic Organic Cotton T-Shirt Optical White   
20211021KnowtheOrigin39        Nicole Recycled Sustainable Sunglasses Black   
20211021KnowtheOrigin40          Abstract Bone Organic Cotton T-Shirt White   
20211021KnowtheOrigin41         Vik Recycled Sustainable Sunglasses Leopard   
20211021KnowtheOrigin42   Regular Bryce Organic & Recycled Cotton Strong...   
20211021KnowtheOrigin43          Classic Organic Cotton T-Shirt Dusty Olive   
20211021KnowtheOrigin44     Organic Cotton Short Sleeved T-Shirt Lily Green   
20211021KnowtheOrigin45          Breda Recycled Polyester Jacket Dark Khaki   
20211021KnowtheOrigin46               Challenge Vegan Leather Trainer Black   
20211021KnowtheOrigin47           Organic Cotton Pink Melange Flannel Shirt   
20211021KnowtheOrigin48                 Basic Crew Neck Lambswool Knit Grey   
20211021KnowtheOrigin49           

In [301]:
df2 = df2.rename(columns={'image_link_color_new': 'image_link_color'})

In [303]:
df2

display_name  \
clothing_id                                                                   
20211021KnowtheOrigin0                       Ecru Organic Cotton Sweatshirt   
20211021KnowtheOrigin1          #3001 Organic Cotton Button Overshirt Khaki   
20211021KnowtheOrigin2           #3003 Organic Cotton Button Overshirt Navy   
20211021KnowtheOrigin3      #5005 Organic Cotton Workwear Pants Faded Black   
20211021KnowtheOrigin4              Heavyweight Organic Cotton T-shirt Bark   
20211021KnowtheOrigin5                     Organic Cotton Oxford Shirt Blue   
20211021KnowtheOrigin6                    Organic Cotton Boxers 2-Pack Grey   
20211021KnowtheOrigin7                  Organic Cotton T-Shirt Navy Striped   
20211021KnowtheOrigin8    Regular Dunn Organic & Recycled Cotton Black J...   
20211021KnowtheOrigin9                 SilverTech Active White Tennis Socks   
20211021KnowtheOrigin10                    Rovigo Organic Cotton Navy Shirt   
20211021KnowtheOrigin11   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
20211021KnowtheOrigin12   Clean Clothes Campaign X KTO - Fairtrade Organ...   
20211021KnowtheOrigin13   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
20211021KnowtheOrigin14    Heavyweight Organic Cotton T-shirt Blue Graphite   
20211021KnowtheOrigin15               Emanuele Organic Cotton Navy Trousers   
20211021KnowtheOrigin16   Heavyweight Organic Cotton Long Sleeve T-Shirt...   
20211021KnowtheOrigin17            Heavyweight Organic Cotton T-shirt White   
20211021KnowtheOrigin18                     Arthur Bamboo Boxer Shorts Grey   
20211021KnowtheOrigin19            Organic Cotton Flannel Shirt Pale Yellow   
20211021KnowtheOrigin20                  Organic Cotton Sweatshirt Burgundy   
20211021KnowtheOrigin21           #5005 Organic Cotton Workwear Pants Khaki   
20211021KnowtheOrigin22          Organic Cotton Short Sleeved T-Shirt White   
20211021KnowtheOrigin23              Emanuele Organic Cotton Trousers Khaki   
20211021KnowtheOrigin24    Bes Microcorduroy Organic Cotton Overshirt Camel   
20211021KnowtheOrigin25                             Mark Jacket Olive Green   
20211021KnowtheOrigin26   Finley Gots Cotton Boxer & Sock Gift Box (6 Pack)   
20211021KnowtheOrigin27                     Mark Organic Cotton Jacket Navy   
20211021KnowtheOrigin28     Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin29         Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin30             Modelo 89' Recycled Vegan Trainer White   
20211021KnowtheOrigin31   Choose Love X KTO - Fairtrade Organic Cotton T...   
20211021KnowtheOrigin32   Mind X KTO - Fairtrade Organic Cotton T-Shirt ...   
20211021KnowtheOrigin33               Kopfkino Organic Cotton T-Shirt Black   
20211021KnowtheOrigin34   Côte Des Basques Recycled Sustainable Sunglass...   
20211021KnowtheOrigin35      Modelo 89' Recycled Vegan Trainer Grey & White   
20211021KnowtheOrigin36                 Basic Crew Neck Lambswool Knit Blue   
20211021KnowtheOrigin37   Barnabus X KTO - Fairtrade Organic Cotton T-Sh...   
20211021KnowtheOrigin38        Classic Organic Cotton T-Shirt Optical White   
20211021KnowtheOrigin39        Nicole Recycled Sustainable Sunglasses Black   
20211021KnowtheOrigin40          Abstract Bone Organic Cotton T-Shirt White   
20211021KnowtheOrigin41         Vik Recycled Sustainable Sunglasses Leopard   
20211021KnowtheOrigin42   Regular Bryce Organic & Recycled Cotton Strong...   
20211021KnowtheOrigin43          Classic Organic Cotton T-Shirt Dusty Olive   
20211021KnowtheOrigin44     Organic Cotton Short Sleeved T-Shirt Lily Green   
20211021KnowtheOrigin45          Breda Recycled Polyester Jacket Dark Khaki   
20211021KnowtheOrigin46               Challenge Vegan Leather Trainer Black   
20211021KnowtheOrigin47           Organic Cotton Pink Melange Flannel Shirt   
20211021KnowtheOrigin48                 Basic Crew Neck Lambswool Knit Grey   
20211021KnowtheOrigin49           

In [304]:
KnowtheOrigin_table = pd.concat([df,df2])

In [305]:
KnowtheOrigin_table

display_name  \
clothing_id                                                                   
20211021KnowtheOrigin0                        Topanga Recycled PET Bra Plum   
20211021KnowtheOrigin1                Flora Organic Cotton Check Dress Navy   
20211021KnowtheOrigin2          Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin3      Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin4                Handy 100% Recycled PET Backpack Rust   
20211021KnowtheOrigin5                Handy 100% Recycled PET Backpack Pink   
20211021KnowtheOrigin6               Handy 100% Recycled PET Backpack Lilac   
20211021KnowtheOrigin7          Juliette Organic Cotton Checked Shirt Brown   
20211021KnowtheOrigin8           Joy Organic Cotton Corduroy Dungarees Lion   
20211021KnowtheOrigin9                  360° PET Sherpa Unisex Jacket Black   
20211021KnowtheOrigin10                         Hera Knitted Sweater Orange   
20211021KnowtheOrigin11                    WUKA Basics Hipster Period Pants   
20211021KnowtheOrigin12                  Modelo 89' Trainer Green and White   
20211021KnowtheOrigin13                  Modelo 89' Trainer Beige and White   
20211021KnowtheOrigin14              Hallie Wildflower Organic Cotton Dress   
20211021KnowtheOrigin15             Modelo 89' Recycled Vegan Trainer White   
20211021KnowtheOrigin16   Choose Love X KTO - Fairtrade Organic Cotton T...   
20211021KnowtheOrigin17   Recycled PET High-Rise Compressive Pocket Legg...   
20211021KnowtheOrigin18                Eva Organic Bamboo G-String Charcoal   
20211021KnowtheOrigin19                     Stella Mauve Low Cut Bamboo Bra   
20211021KnowtheOrigin20              Frankie Organic Bamboo Flares Charcoal   
20211021KnowtheOrigin21                     Stella Olive Low Cut Bamboo Bra   
20211021KnowtheOrigin22                      Kata Organic Cotton Dress Navy   
20211021KnowtheOrigin23   WUKA Organic Cotton Bikini Period Pants - Medi...   
20211021KnowtheOrigin24   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin25   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin26                       Erin Woven Hemp Jumpsuit Navy   
20211021KnowtheOrigin27                  Stella Charcoal Low Cut Bamboo Bra   
20211021KnowtheOrigin28                              Lodi Modal Dress Black   
20211021KnowtheOrigin29   Côte Des Basques Recycled Sustainable Sunglass...   
20211021KnowtheOrigin30         Priti Organic Cotton Cross Back Dress Black   
20211021KnowtheOrigin31               Leonie Organic Cotton Dress Off White   
20211021KnowtheOrigin32              Leo Organic Bamboo High-Cut Bra Cherry   
20211021KnowtheOrigin33   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin34                        Sunny Side Modal Dress Black   
20211021KnowtheOrigin35        Classic Organic Cotton T-Shirt Optical White   
20211021KnowtheOrigin36                 Ana Organic Cotton Knit Pants Black   
20211021KnowtheOrigin37      Modelo 89' Recycled Vegan Trainer Grey & White   
20211021KnowtheOrigin38             Essential Organic Cotton Black Leggings   
20211021KnowtheOrigin39             Aidin Hemp Loose Fit T-Shirt Dark Green   
20211021KnowtheOrigin40             Recycled PET High-Rise Bike Short Black   
20211021KnowtheOrigin41                       Paloma Recycled PET Bra Black   
20211021KnowtheOrigin42   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin43   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin44                Evelyn Organic Cotton Black Jumpsuit   
20211021KnowtheOrigin45                              Orli Modal Dress Black   
20211021KnowtheOrigin46            Laila Organic Cotton Roll Neck Black Top   
20211021KnowtheOrigin47                  Eva Organic Bamboo G-String Cherry   
20211021KnowtheOrigin48                                  Bumi Leotard Black   
20211021KnowtheOrigin49           

In [307]:
len(KnowtheOrigin_table)

971

In [312]:
df = KnowtheOrigin_table.rename(columns={'product_material': 'fabric'})

In [313]:
df

display_name  \
clothing_id                                                                   
20211021KnowtheOrigin0                        Topanga Recycled PET Bra Plum   
20211021KnowtheOrigin1                Flora Organic Cotton Check Dress Navy   
20211021KnowtheOrigin2          Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin3      Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin4                Handy 100% Recycled PET Backpack Rust   
20211021KnowtheOrigin5                Handy 100% Recycled PET Backpack Pink   
20211021KnowtheOrigin6               Handy 100% Recycled PET Backpack Lilac   
20211021KnowtheOrigin7          Juliette Organic Cotton Checked Shirt Brown   
20211021KnowtheOrigin8           Joy Organic Cotton Corduroy Dungarees Lion   
20211021KnowtheOrigin9                  360° PET Sherpa Unisex Jacket Black   
20211021KnowtheOrigin10                         Hera Knitted Sweater Orange   
20211021KnowtheOrigin11                    WUKA Basics Hipster Period Pants   
20211021KnowtheOrigin12                  Modelo 89' Trainer Green and White   
20211021KnowtheOrigin13                  Modelo 89' Trainer Beige and White   
20211021KnowtheOrigin14              Hallie Wildflower Organic Cotton Dress   
20211021KnowtheOrigin15             Modelo 89' Recycled Vegan Trainer White   
20211021KnowtheOrigin16   Choose Love X KTO - Fairtrade Organic Cotton T...   
20211021KnowtheOrigin17   Recycled PET High-Rise Compressive Pocket Legg...   
20211021KnowtheOrigin18                Eva Organic Bamboo G-String Charcoal   
20211021KnowtheOrigin19                     Stella Mauve Low Cut Bamboo Bra   
20211021KnowtheOrigin20              Frankie Organic Bamboo Flares Charcoal   
20211021KnowtheOrigin21                     Stella Olive Low Cut Bamboo Bra   
20211021KnowtheOrigin22                      Kata Organic Cotton Dress Navy   
20211021KnowtheOrigin23   WUKA Organic Cotton Bikini Period Pants - Medi...   
20211021KnowtheOrigin24   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin25   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin26                       Erin Woven Hemp Jumpsuit Navy   
20211021KnowtheOrigin27                  Stella Charcoal Low Cut Bamboo Bra   
20211021KnowtheOrigin28                              Lodi Modal Dress Black   
20211021KnowtheOrigin29   Côte Des Basques Recycled Sustainable Sunglass...   
20211021KnowtheOrigin30         Priti Organic Cotton Cross Back Dress Black   
20211021KnowtheOrigin31               Leonie Organic Cotton Dress Off White   
20211021KnowtheOrigin32              Leo Organic Bamboo High-Cut Bra Cherry   
20211021KnowtheOrigin33   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin34                        Sunny Side Modal Dress Black   
20211021KnowtheOrigin35        Classic Organic Cotton T-Shirt Optical White   
20211021KnowtheOrigin36                 Ana Organic Cotton Knit Pants Black   
20211021KnowtheOrigin37      Modelo 89' Recycled Vegan Trainer Grey & White   
20211021KnowtheOrigin38             Essential Organic Cotton Black Leggings   
20211021KnowtheOrigin39             Aidin Hemp Loose Fit T-Shirt Dark Green   
20211021KnowtheOrigin40             Recycled PET High-Rise Bike Short Black   
20211021KnowtheOrigin41                       Paloma Recycled PET Bra Black   
20211021KnowtheOrigin42   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin43   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin44                Evelyn Organic Cotton Black Jumpsuit   
20211021KnowtheOrigin45                              Orli Modal Dress Black   
20211021KnowtheOrigin46            Laila Organic Cotton Roll Neck Black Top   
20211021KnowtheOrigin47                  Eva Organic Bamboo G-String Cherry   
20211021KnowtheOrigin48                                  Bumi Leotard Black   
20211021KnowtheOrigin49           

In [315]:
##### get mapped_id
GranRegs = pd.read_csv('MaterialProxy.csv', header=None, skiprows=[0])
GranRegs = GranRegs.drop(columns=[1])
GranRegs.columns = list(range(len(GranRegs.columns)))

In [309]:
#extract materials

def extractMaterials(df):
    fabric_text = df['fabric']
    fabric_text = str(fabric_text).replace('solvent', '').replace('Grown', '').replace('grown', '').replace('organically', 'organic').replace('Organically', 'organic')
    splitted_fabric = fabric_text.replace("'", '').replace("[", '').replace("]", '').replace(",", '').replace('’', '').replace('.', '').replace('–', '').replace('-', '').split()
    pattern = "\d{1,3}[$%]"
    
    description_text = df['description'] + df['display_name'] + df['fabric']
    description_text = str(description_text).replace('solvent', '').replace('Grown', '').replace('grown', '').replace('organically', 'organic').replace('Organically', 'organic')
    splitted_description = description_text.replace("'", '').replace("[", '').replace("]", '').replace(",", '').replace('’', '').replace('.', '').replace('–', '').replace('-', '')
    pattern = "\d{1,3}[$%]"
    
    mat_list = []
    extra_materials = []
    
    
    ## getting the materials regex matching
    subRegs = GranRegs.iloc[:, 1:]
    Regs = []
    materialsReg = []
    for index, row in subRegs.iterrows():
        for i in range(1,len(GranRegs.columns)):
            if pd.isnull(row[i]): continue
            else: Regs.append(row[i])
    total_percentage = [] 
    is_no_percentage = True 
    for i in range(len(splitted_fabric)):
        if re.fullmatch(pattern,splitted_fabric[i]):
            total_percentage.append(float(splitted_fabric[i].replace("%", '')))
            if sum(total_percentage) <= 100:
            
                if splitted_fabric[i+1].lower() == 'organic':
                    mat_list.append(splitted_fabric[i] + ' ' + splitted_fabric[i+1].lower() + ' ' + splitted_fabric[i+2].lower())
                    is_no_percentage = False
                    
                elif splitted_fabric[i+1].lower() == 'recycled':
                    mat_list.append(splitted_fabric[i] + ' ' + splitted_fabric[i+1].lower() + ' ' + splitted_fabric[i+2].lower())
                    is_no_percentage = False
                
                elif splitted_fabric[i+1].lower() == 'tencel™':
                    mat_list.append(splitted_fabric[i] + ' ' + splitted_fabric[i+1].lower() + ' ' + splitted_fabric[i+2].lower())
                    is_no_percentage = False
                    
                else:
                    if splitted_fabric[i] + ' ' + splitted_fabric[i+1].lower() not in mat_list:
                        mat_list.append(splitted_fabric[i] + ' ' + splitted_fabric[i+1].lower())
                        is_no_percentage = False
                        
    if sum(total_percentage) < 100 or is_no_percentage == True:
        for reg in Regs:
            #print(splitted_description.lower())
            if re.search(reg, splitted_description.lower()):
                match = re.search(reg, splitted_description.lower())
                matched_material = splitted_description[match.start():match.end()].lower()
                
                if matched_material not in extra_materials:
                    extra_materials.append(matched_material)
    
    #print(extra_materials)
    if len(extra_materials)>1:
        if "cotton" in extra_materials and "organic cotton" in extra_materials:
            mat_list.append("100% organic cotton")
        if "leather" in extra_materials:
            mat_list.append("100% leather")
    elif len(extra_materials)!=0:
        mat_list.append("100% " + extra_materials[0])

            
    
    return mat_list



In [316]:
df['materials'] = df.apply(lambda x: extractMaterials(x), axis=1)

In [317]:
df[df["materials"].str.len() == 0]['fabric']

clothing_id
20211021KnowtheOrigin29     Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin61     Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin111    Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin119    Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin146    Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin171    Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin259    \nAll Ilk and Ernie fabrics are hand sourced f...
20211021KnowtheOrigin260    Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin261    Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin271    \nAll Ilk and Ernie fabrics are hand sourced f...
20211021KnowtheOrigin291    Unisex style with UV 400 protection. Blocks ou...
20211021KnowtheOrigin327    \nAll Ilk and Ernie fabrics are hand sourced f...
20211021KnowtheOrigin413    \nAll Ilk and Ernie fabr

In [319]:
df = df.rename(columns={'materials':'product_material'})

In [327]:
df = pd.read_csv('KnowtheOrigin_table.csv')

In [331]:
df=df.drop(['image_link_color'], axis=1)

In [333]:
df = df.rename(columns={'image_link_color.1':'image_link_color'})

In [335]:
df = df.set_index('clothing_id')

In [336]:
df

display_name  \
clothing_id                                                                   
20211021KnowtheOrigin0                        Topanga Recycled PET Bra Plum   
20211021KnowtheOrigin1                Flora Organic Cotton Check Dress Navy   
20211021KnowtheOrigin2          Modelo 89' Recycled Vegan Trainer Off White   
20211021KnowtheOrigin3      Modelo 89' Recycled Vegan Trainer Beige & White   
20211021KnowtheOrigin4                Handy 100% Recycled PET Backpack Rust   
20211021KnowtheOrigin5                Handy 100% Recycled PET Backpack Pink   
20211021KnowtheOrigin6               Handy 100% Recycled PET Backpack Lilac   
20211021KnowtheOrigin7          Juliette Organic Cotton Checked Shirt Brown   
20211021KnowtheOrigin8           Joy Organic Cotton Corduroy Dungarees Lion   
20211021KnowtheOrigin9                  360° PET Sherpa Unisex Jacket Black   
20211021KnowtheOrigin10                         Hera Knitted Sweater Orange   
20211021KnowtheOrigin11                    WUKA Basics Hipster Period Pants   
20211021KnowtheOrigin12                  Modelo 89' Trainer Green and White   
20211021KnowtheOrigin13                  Modelo 89' Trainer Beige and White   
20211021KnowtheOrigin14              Hallie Wildflower Organic Cotton Dress   
20211021KnowtheOrigin15             Modelo 89' Recycled Vegan Trainer White   
20211021KnowtheOrigin16   Choose Love X KTO - Fairtrade Organic Cotton T...   
20211021KnowtheOrigin17   Recycled PET High-Rise Compressive Pocket Legg...   
20211021KnowtheOrigin18                Eva Organic Bamboo G-String Charcoal   
20211021KnowtheOrigin19                     Stella Mauve Low Cut Bamboo Bra   
20211021KnowtheOrigin20              Frankie Organic Bamboo Flares Charcoal   
20211021KnowtheOrigin21                     Stella Olive Low Cut Bamboo Bra   
20211021KnowtheOrigin22                      Kata Organic Cotton Dress Navy   
20211021KnowtheOrigin23   WUKA Organic Cotton Bikini Period Pants - Medi...   
20211021KnowtheOrigin24   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin25   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin26                       Erin Woven Hemp Jumpsuit Navy   
20211021KnowtheOrigin27                  Stella Charcoal Low Cut Bamboo Bra   
20211021KnowtheOrigin28                              Lodi Modal Dress Black   
20211021KnowtheOrigin29   Côte Des Basques Recycled Sustainable Sunglass...   
20211021KnowtheOrigin30         Priti Organic Cotton Cross Back Dress Black   
20211021KnowtheOrigin31               Leonie Organic Cotton Dress Off White   
20211021KnowtheOrigin32              Leo Organic Bamboo High-Cut Bra Cherry   
20211021KnowtheOrigin33   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin34                        Sunny Side Modal Dress Black   
20211021KnowtheOrigin35        Classic Organic Cotton T-Shirt Optical White   
20211021KnowtheOrigin36                 Ana Organic Cotton Knit Pants Black   
20211021KnowtheOrigin37      Modelo 89' Recycled Vegan Trainer Grey & White   
20211021KnowtheOrigin38             Essential Organic Cotton Black Leggings   
20211021KnowtheOrigin39             Aidin Hemp Loose Fit T-Shirt Dark Green   
20211021KnowtheOrigin40             Recycled PET High-Rise Bike Short Black   
20211021KnowtheOrigin41                       Paloma Recycled PET Bra Black   
20211021KnowtheOrigin42   Float Seamless Lightweight Recycled PET High-R...   
20211021KnowtheOrigin43   Cleo Float Seamless Lightweight Recycled PET S...   
20211021KnowtheOrigin44                Evelyn Organic Cotton Black Jumpsuit   
20211021KnowtheOrigin45                              Orli Modal Dress Black   
20211021KnowtheOrigin46            Laila Organic Cotton Roll Neck Black Top   
20211021KnowtheOrigin47                  Eva Organic Bamboo G-String Cherry   
20211021KnowtheOrigin48                                  Bumi Leotard Black   
20211021KnowtheOrigin49           

In [337]:
df.to_csv('KnowtheOrigin_table.csv')

In [ ]:
# Other trial and error attemps

In [40]:
page = BeautifulSoup(requests.get("https://knowtheorigin.com/collections/women").content,'lxml')

In [42]:
page.find('div',class_="row collection-view-three")

<div class="row collection-view-three" id="bc-sf-filter-products">
<!--

<secttion class="product-single col standard-product">
    

        
    
    <div class="product-image product-image-hover"> 
        <a href="/products/seville-hoops-gold" class="fixed-ratio collection-portrait-crop">
            
            <img class="" src="//cdn.shopify.com/s/files/1/2364/4077/products/seville-gold-hoops-accessories-womens-little-by-little-116767_500x.jpg?v=1613695374" data-src="//cdn.shopify.com/s/files/1/2364/4077/products/seville-gold-hoops-accessories-womens-little-by-little-116767_500x.jpg?v=1613695374" data-srcset="//cdn.shopify.com/s/files/1/2364/4077/products/seville-gold-hoops-accessories-womens-little-by-little-116767_500x.jpg?v=1613695374 500w, //cdn.shopify.com/s/files/1/2364/4077/products/seville-gold-hoops-accessories-womens-little-by-little-116767_500x.jpg?v=1613695374 500w, //cdn.shopify.com/s/files/1/2364/4077/products/seville-gold-hoops-accessories-womens-little-by-little

In [44]:
page.find('span',class_="product-image product-image-hover")

In [ ]:
product-image product-image-hover

In [140]:
page.find('div',class_="product-details")

In [42]:
page1 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/flora-check-dress-navy").content,'lxml')

In [43]:
try:
    details = page1.find('div',class_='tab materials').find('div').get_text()
except:
    details = page1.find('div',class_='tab description').find_all('p')[-1].get_text()

In [44]:
details

'100% Organic Cotton'

In [133]:
try:
    details = page1.find('div',class_='tab materials').find('div').get_text()
except:
    try:
        details = page1.find('div',class_='tab description').find_all('p')
        for item in details:
            mat = item.get_text()
            if "%" in mat:
                materials = mat
            else:
                pass
    except:
        details = page1.find('div',class_="tab product-description").find_all('p')
        for item in details:
            mat = item.get_text()
            if "%" in mat:
                materials = mat
            else:
                pass

In [134]:
materials

'100% Organic Cotton'

In [45]:
"%" in details

True

In [81]:
size = []
size_class = page1.find('div',class_="swatch swatch-size clearfix").find_all('label')
for item in size_class:
    s=item.get_text().strip()
    size.append(s)
size = json.dumps(size)

In [82]:
size

'["XS", "S", "M", "L", "XL"]'

In [88]:
page1.find('span',class_="product-detail-price observe").find('span',class_="money").get_text()

'£95.00'

In [96]:
description = ''
des = page1.find('div',class_="tab description").find_all('p')
for item in des:
    line = item.get_text().strip()
    description += line

In [97]:
description

'Loose fit navy turtleneck dress in check print with statement balloon sleeves.Thinking Mu only use organic, up-cycled or recycled fibres and fabrics in all of their collections. The dyeing process is natural, low-impact and biodegradable. The printing technique is digital, water-based and biodegradable.Organic Cotton facilitates the future recycling of the product. Organic certificates by GOTS (Global Organic Textile Standards)\xa0helps protect the farmers with healthy soil.100% Organic Cotton'

In [93]:
page1.find('div',class_="tab description").find_all('p')[0].get_text()

'Loose fit navy turtleneck dress in check print with statement balloon sleeves.'

In [38]:
page2 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/copy-of-modelo-89-recycled-vegan-trainer-white").content,'lxml')

In [41]:
page2.find('div',class_='tab materials').find('div').get_text()

'\n\xa0>Upper: recycled vegan napa (GRS): 35% RPET, 11% polyester, 54% high-solid PU.> Lining: recycled post-consumer PET (GRS): 50% RPET and 50% PES. > Removable insole: 60% recycled PU foam from automotive leftovers and 40% PU foam.> Outsole: natural 30% and synthetic 70% rubber mix.> Laces: certified organic cotton.> Reinforcements: 65% recycled thermoplastic and 35% wood chips.> Packaging: recycled box and paper / plastic free & fully biodegradable bag. '

In [79]:
size = []
size_class = page2.find('div',class_="swatch swatch-size clearfix").find_all('label')
for item in size_class:
    s=item.get_text().strip()
    size.append(s)
size = json.dumps(size)

In [80]:
size

'["36", "37", "38", "39", "40", "41", "42", "43", "44", "45"]'

In [89]:
page2.find('span',class_="product-detail-price observe").find('span',class_="money").get_text()

'£125.00'

In [98]:
description = ''
des = page2.find('div',class_="tab description").find_all('p')
for item in des:
    line = item.get_text().strip()
    description += line

In [99]:
description

"The Model 89 is the signature style from 80s inspired footwear brand Saye and is\xa0the best-looking retro-inspired trainer out there! This off-white style is part of their Vegan range is manufactured using PU made from recycled post-consumer fibers. As well as the recycled upper the Vegan Model 89' comes with sustainable cotton linings and laces, as well as natural rubber-mix outsoles and reinforcements made from wood chips. The Modelo 89 is both sustainable\xa0and stylish."

In [136]:
page2.find('form')

<form action="/search" class="site-search" method="get" role="search">
<label class="label-hidden">
		Search
	</label>
<input name="q" placeholder="Search" type="search" value=""/>
<button type="submit">
<span>&gt;</span>
<span class="icon-fallback-text">Search</span>
</button>
</form>

In [55]:
page3 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/recycled-pet-high-rise-compressive-pocket-leggings-dark-green").content,'lxml')

In [49]:
try:
    details = page3.find('div',class_='tab materials').find('div').get_text()
except:
    try:
        details = page3.find('div',class_='tab description').find_all('p')[-1].get_text()
    except:
        details = page3.find('div',class_="tab product-description").find_all('p')[-1].get_text()

In [52]:
details

'Made from 79% recycled plastic bottles (RPET) and 21% spandex'

In [59]:
page3.find('h1',class_='product-title').get_text()

'Recycled PET High-Rise Compressive Pocket Leggings Black'

In [77]:
size = []
size_class = page3.find('div',class_="swatch swatch-size clearfix").find_all('label')
for item in size_class:
    s=item.get_text().strip()
    size.append(s)
size = json.dumps(size)

In [78]:
size

'["XS", "S", "M", "L", "XL", "XXL", "XXXL"]'

In [87]:
page3.find('span',class_="product-detail-price observe").find('span',class_="money").get_text()

'£65.00'

In [104]:
description = ''
try:
    des = page3.find('div',class_="tab description").find_all('p')
    for item in des:
        line = item.get_text().strip()
        description += line
except:
    description = page3.find('div',class_="tab product-description").find_all('p')[0].get_text()

In [105]:
description

'The recycled polyester legging designed with high-impact activities in mind. This classic style has sweat wicking properties and a high-rise waist, that does not roll, and\xa0a pocket on each hip for your phone, wallet, keys or whatever else you feel like putting in there. The durable recycled polyester and elastane blend is made from recycled water bottles, providing four way stretch and a supportive compressive fit.'

In [103]:
page3.find('div',class_="tab product-description").find_all('p')[0].get_text()

'The recycled polyester legging designed with high-impact activities in mind. This classic style has sweat wicking properties and a high-rise waist, that does not roll, and\xa0a pocket on each hip for your phone, wallet, keys or whatever else you feel like putting in there. The durable recycled polyester and elastane blend is made from recycled water bottles, providing four way stretch and a supportive compressive fit.'

In [106]:
page4 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/float-seamless-lightweight-recycled-pet-high-rise-leggings-black").content,'lxml')

In [107]:
description = ''
try:
    des = page4.find('div',class_="tab description").find_all('p')
    for item in des:
        line = item.get_text().strip()
        description += line
except:
    description = page4.find('div',class_="tab product-description").find_all('p')[0].get_text()
if not description:
    try:
        description = page4.find('div',class_="tab description").find('span').get_text()
    except:
        description = page4.find('div',class_="tab product-description").find_all('p')[0].get_text()
if not description:
    try:
        description = page4.find('div',class_='tab description').get_text().strip()
    except:
        pass

In [112]:
page4.find('div',class_="tab description").find('span').get_text()

"In case you need something lighter weight for hot days, hot workouts or just looking hot lounging around — the FLOAT High-Rise Legging. They're stretchy and comfy enough for max-relaxing but sturdy enough for working out. Toss them on to lounge around and boom, you’re already dressed for that run you may or may not go on.> Made from 90% recycled plastic bottles (RPET) and 10% spandex> Recyclable with ReGirlfriend> Lightweight, yet substantial — perfect for all workouts and activities> Sweat-wicking and quick-drying> Sheer-proof> Buttery soft hand feel> Brushed matte finish> Small hidden back pocket for keys or cards> UPF 50+"

In [115]:
try:
    details = page4.find('div',class_='tab materials').find('div').get_text()
except:
    try:
        details = page4.find('div',class_='tab description').find_all('p')
        for item in details:
            if "%" in item:
                materials = details
            else:
                pass
    except:
        details = page4.find('div',class_="tab product-description").find_all('p')
        for item in details:
            if "%" in item:
                materials = details
            else:
                pass

In [117]:
materials

'100% Organic Cotton'

In [120]:
page5 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/float-seamless-lightweight-recycled-pet-high-rise-bike-short-black").content,'lxml')

In [127]:
try:
    details = page5.find('div',class_='tab materials').find('div').get_text()
except:
    try:
        details = page5.find('div',class_='tab description').find_all('p')
        for item in details:
            mat = item.get_text()
            if "%" in mat:
                materials = mat
            else:
                pass
    except:
        details = page5.find('div',class_="tab product-description").find_all('p')
        for item in details:
            mat = item.get_text()
            if "%" in mat:
                materials = mat
            else:
                pass

In [128]:
materials

'> Made from 90% recycled plastic bottles (RPET) and 10% spandex> Recyclable with ReGirlfriend> Lightweight, yet substantial — perfect for all workouts and activities> Sweat-wicking and quick-drying> Sheer-proof> Buttery soft hand feel> Brushed matte finish> Small hidden back pocket for keys or cards> UPF 50+\xa0'

In [192]:
page6 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/handy-100-recycled-pet-backpack-rust").content,'lxml')

In [197]:
page6.find('div',class_='tab description').get_text().strip()

'The stylishly simple Handy Backpack is one of Lefrik’s best-selling items. Its slim profile comfortably fits a 15” laptop and the water-resistant fabric makes it the perfect choice for daily commuting.The Handy comes with a double strap closure to main compartment\xa0and features an inside zippered pocket.'

In [213]:
page7 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/joy-organic-cotton-corduroy-dungarees-lion").content,'lxml')

In [216]:
page7.find('div',class_='tab material').get_text().strip()

'100% GOTS Certified Organic Cotton Corduroy'

In [218]:
page8 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/ana-organic-cotton-knit-pants-black").content,'lxml')

In [220]:
page8.find('div',class_='tab material').get_text().strip()

'100% organic cotton/Bio-Baumwolle'

In [221]:
page9 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/float-seamless-lightweight-recycled-pet-high-rise-leggings-midnight").content,'lxml')

In [228]:
lines = page9.find('div',class_='tab description').find('span').get_text().split('> ')
for l in lines:
    if '%' in l:
        materials = l

In [229]:
materials

'Made from 90% recycled plastic bottles (RPET) and 10% spandex'

In [236]:
page10 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/juliet-float-seamless-lightweight-recycled-pet-sports-bra-midnight").content,'lxml')

In [232]:
lines = page10.find('div',class_='tab product-description').find('span').get_text().split('> ')
for l in lines:
    if '%' in l:
        materials = l

In [233]:
materials

'Made from 90% recycled plastic bottles (RPET) and 10% spandex'

In [237]:
page11 = BeautifulSoup(requests.get("https://knowtheorigin.com/products/sona-organic-cotton-heavy-knit-jumper-grey-melange").content,'lxml')

In [239]:
lines = page11.find('div',class_='tab description').get_text().split('> ')
for l in lines:
    if '%' in l:
        materials = l

In [246]:
lines = page11.find('div',class_='tab description').get_text().strip().split('\xa0')
for l in lines:
    if '%' in l:
        materials = l

In [247]:
materials

'100% organic cotton knit/Bio-BaumwollstrickFit: Relaxed / Loose fit\n'

In [67]:
pip install selenium

     |████████████████████████████████| 954 kB 8.6 MB/s eta 0:00:01
     |████████████████████████████████| 356 kB 6.0 MB/s eta 0:00:01
     |████████████████████████████████| 54 kB 8.8 MB/s  eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [68]:
from bs4 import BeautifulSoup
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.support.ui import WebDriverWait
from selenium.common.exceptions import TimeoutException

In [69]:
def configure_driver():
    # Add additional Options to the webdriver
    chrome_options = Options()
    # add the argument and make the browser Headless.
    chrome_options.add_argument("--headless")
    # Instantiate the Webdriver: Mention the executable path of the webdriver you have downloaded
    # For linux/Mac
    driver = webdriver.Chrome(options = chrome_options)
    # For windows
    # driver = webdriver.Chrome(executable_path="./chromedriver.exe", options = chrome_options)
    return driver

In [ ]:
def get_details(product_link):
    page = BeautifulSoup(requests.get(product_link).content,'lxml')
    
    # Retrieve product materials
    details = page.find('div', class_="product-description-short rte-content").find_all('li')
    # Create an empty product_material dictionary
    product_material = {}
    for item in details:
        text = item.get_text()
        if "Main fabric" in text:
            materials = text.strip().split("Main fabric: ")[1].split(" / ")
            for item in materials:
                pct = item.split('%')[0]
                pct = f'{pct}%'
                mtr = item.split('%')[1]
                product_material[str(mtr)]=pct
    product_material = json.dumps(product_material)
    
    # Create an empty color list
    color = []
    # Create an empty image_link_color dictionary
    image_link_color = {}
    # Retrieve available colors if multiple colors are offered
    try:
        color_class = page.find('div', class_="block-content d-flex justify-content-center justify-content-md-start mb-2 mt-3").find_all('a')
        for item in color_class:
            link = item.get('href')
            image = BeautifulSoup(requests.get(link).content,'lxml').find('div', class_="product-lmage-large swiper-slide").find('a').get('href')
            c = item.get('title').strip()
            # Store available colors in color list
            color.append(c)
            # Store color-link pairs in image_link_color dictionary
            image_link_color[str(c)]=image
            
    # Retrieve single color if only single color is offered
    except:
        c = page.find('div',class_="nomcolor text-capitalize mb-4 text-center text-md-left").get_text()
        color.append(c)
        try:
            image = page.find('div', class_="product-lmage-large swiper-slide").find('a').get('href')
            image_link_color[str(c)]=image
        except:
            image_link_color[str(c)]=None
    color = json.dumps(color)
    image_link_color = json.dumps(image_link_color)
    
        
    # Retrieve available sizes
    size_class = page.find_all('li',class_="input-container float-left")
    # Create an empty size list
    size = []
    for item in size_class:
        s = item.find('span').get_text()
        size.append(s)
    size = json.dumps(size)
        
    # Retrieve price
    price = page.find('span', class_="product-price").get_text()
    price = price.split('$')[1]
    price = f'USD {price}'
    
    # Retrieve description
    description = page.find('div',class_="product-description text-left").find('div',class_="rte-content").get_text().strip()
        
    return product_material, color, image_link_color, size, price, description